# Working with large datasets

In [1]:
%%capture --no-display
from dask.distributed import Client
client = Client(address = 'tcp://192.168.62.207:8786')
client

<Client: 'tcp://192.168.62.207:8786' processes=10 threads=120, memory=673.47 GB>

In [2]:
%%time
import takco
# ts = takco.DaskHashBag.load(f'hdfs://bricks07:9000/user/kruit/tabel/1.jsonl')
ts = takco.HashBag.load('../../data/TabEL/75k-part/75k-part-aa')
ts = takco.TableSet.reshape(ts)
ts = takco.TableSet.number_table_columns(ts)
ts.persist()
# ts.bag.count().compute()

CPU times: user 4.85 s, sys: 295 ms, total: 5.14 s
Wall time: 5.16 s


In [3]:
%%time
i_table = {t['tableIndex']:t for t in ts}
print(len(i_table))

1486
CPU times: user 1.51 ms, sys: 177 µs, total: 1.69 ms
Wall time: 1.4 ms


In [4]:
%%time
from takco.cluster.matchers import LSHMatcher, EmbeddingMatcher
from takco import cluster
matchers = [LSHMatcher('.'), EmbeddingMatcher('.', wordvec_fname='/export/scratch1/home/kruit/glove.6B.50d.pickle')]

matchers = ts.pipe(cluster.matcher_add_tables, matchers)
matchers = list(matchers.fold(lambda x: x.name, lambda a, b: a.merge(b)))

CPU times: user 5.67 s, sys: 304 ms, total: 5.97 s
Wall time: 5.99 s


In [5]:
%%time
for m in matchers:
    print(m.name)
    m.index()
    print(m.indexed)

Inserting MinHash LSH:   7%|▋         | 311/4772 [00:00<00:01, 3103.37it/s]

LSHMatcher


Inserting MinHash LSH: 100%|██████████| 4772/4772 [00:01<00:00, 2458.91it/s]


True
EmbeddingMatcher
True
CPU times: user 2.76 s, sys: 383 ms, total: 3.15 s
Wall time: 2.98 s


In [6]:
%%time
tableid_colids = {
    i: range(t["columnIndexOffset"], t["columnIndexOffset"] + t["numCols"])
    for i,t in i_table.items()
}

CPU times: user 1.68 ms, sys: 0 ns, total: 1.68 ms
Wall time: 1.69 ms


In [ ]:
%%time
import logging as log
log.getLogger().setLevel(log.DEBUG)

import tqdm
import pandas as pd
df = pd.concat(ts.pipe(
    cluster.get_colsims,
    matchers=matchers,
    agg_func='max',
    agg_threshold=0.5,
    tableid_colids=tableid_colids,
))
df

DEBUG:root:Piping get_colsims ...
INFO:root:Loading word vectors /export/scratch1/home/kruit/glove.6B.50d.pickle
DEBUG:root:Preparing block for matcher LSHMatcher
DEBUG:root:Preparing block for matcher EmbeddingMatcher
DEBUG:root:Querying EmbeddingMatcher faiss index with query matrix of shape (4362, 50)
Matching with EmbeddingMatcher: 100%|██████████| 74169/74169 [00:00<00:00, 161364.91it/s]
DEBUG:root:times: {'prepare-LSHMatcher': 5.0067901611328125e-06, 'prepare-EmbeddingMatcher': 0.5216703414916992, 'block-LSHMatcher': 1.70821213722229, 'block-EmbeddingMatcher': 0.011946678161621094, 'match-LSHMatcher': 7.198833227157593, 'match-EmbeddingMatcher': 3.8893563747406006}
Aggregating column scores:   9%|▉         | 7038/74169 [00:04<00:44, 1501.93it/s]

In [8]:
%%time
block = set()
for m in matchers:
    print(m.name)
    with m:
        block |= set(m.block(0, tableid_colids[0]))
print(f'Got block of size {len(block)}:', block)
takco.preview([i_table[0]] + [i_table[b] for b in block if b in i_table])

LSHMatcher
EmbeddingMatcher
Got block of size 87: {0, 4868, 1285, 4870, 4874, 1557, 791, 1562, 3617, 4385, 3363, 3623, 5163, 5428, 3127, 2619, 5957, 1351, 1612, 1869, 1360, 1872, 1365, 1127, 105, 1130, 5227, 1898, 1903, 2179, 4739, 2948, 138, 4494, 4495, 3987, 1178, 3997, 4001, 1441, 4518, 1196, 4274, 693, 694, 6327, 1208, 1461, 4287, 1219, 3267, 964, 1477, 453, 2508, 4045, 3535, 1488, 4561, 1492, 6101, 2004, 4823, 1495, 4825, 2265, 2266, 1498, 4829, 4827, 1501, 2783, 6111, 1761, 4329, 1513, 4332, 4333, 4846, 4848, 1265, 4852, 1269, 4854, 4856, 1529, 1788}
CPU times: user 663 ms, sys: 336 ms, total: 1e+03 ms
Wall time: 1 s


In [1]:
%%time
import takco, itertools
tables = takco.TableSet.load('../../output/tabel-all/1-reshape/*.jsonl')
# tables = (t for t in tables if 'partColAligns' in t)
n = 10000
tables = list(itertools.islice(tables, n))
tables = sorted(tables, key=lambda x: -x['numDataRows'])
print('Got', len(tables), 'tables')
takco.preview(tables, nrows=10, ntables=50)

Exception ignored in: <generator object HashBag.load.<locals>.it at 0x7f723a8f2250>
RuntimeError: generator ignored GeneratorExit


Got 10000 tables
CPU times: user 9.59 s, sys: 738 ms, total: 10.3 s
Wall time: 10.4 s


In [5]:
%%time
import takco, itertools
tables = takco.TableSet.load('../../output/wikidump-0-99/7-integrate/*.jsonl')
# tables = takco.TableSet.load('../../output/tabel-75k-2/5-cluster/*.jsonl')
# tables = (t for t in tables if 'partColAligns' in t)
n = None
tables = list(itertools.islice(tables, n))
tables = sorted(tables, key=lambda x: -x['numDataRows'])
print('Got', len(tables), 'tables')
takco.preview(tables, nrows=10, ntables=50)

Got 1483 tables
CPU times: user 1min 11s, sys: 4.85 s, total: 1min 16s
Wall time: 1min 16s


In [6]:
print(*tables[1]['tableHeaders'])

In [6]:
takco.preview(tables[0]['partColAligns'])

In [7]:
tables[0]['partColAligns'][1]

{'tableIndex': 5814,
 'partcol_local': {'0': None,
  '1': None,
  '2': 0,
  '3': 1,
  '4': 2,
  '5': None,
  '6': None},
 'partcol_global': {'2': 34002, '3': 34003, '4': 34004},
 '_id': '7704330167631575559-0',
 'tableHeaders': [[{'tdHtmlString': '<th>_pgTitle</th>',
    'text': '_pgTitle',
    'surfaceLinks': []},
   {'text': 'Preceded by'},
   {'text': 'Succeeded by'}]],
 'tableData': [[{'text': 'John of Arborea',
    'tdHtmlString': "<td><a href='/wiki/John of Arborea'>John of Arborea</a></td>",
    'surfaceLinks': [{'offset': 0,
      'endOffset': 15,
      'linkType': 'INTERNAL',
      'target': {'href': 'John of Arborea'}}]},
   {'cellID': -1,
    'textTokens': [],
    'text': 'Marianus II',
    'tdHtmlString': '<td colspan="1" rowspan="2"> Preceded\xa0by <span style="font-weight: bold"> <a href="http://www.wikipedia.org/wiki/Marianus_II_of_Arborea" shape="rect">Marianus II</a></span> </td>',
    'surfaceLinks': [{'offset': 0,
      'endOffset': 11,
      'isInTemplate': False,
 